In [1]:
import glob
from collections import defaultdict
import pandas as pd
import os 
from config import *
import shutil

In [2]:
images_list = glob.glob('face_recognition/lfw_funneled/**/*.jpg',recursive=True)

In [3]:
# Group files by their containing folder
folder_file_map = defaultdict(list)
for file_path in images_list:
    folder = '/'.join(file_path.split('/')[:-1])  # Extract folder path
    folder_file_map[folder].append(file_path)


# Convert defaultdict to a pandas DataFrame
data = []
for folder, files in folder_file_map.items():
    for file in files:
        data.append((folder.split('/')[-1], file))

df = pd.DataFrame(data, columns=["cluster", "file_path"])
df["count"] = df["cluster"].map(df["cluster"].value_counts())
#Filter singletons out
df.query('count>1',inplace=True)
df['picture']=df['file_path'].str.split('/').str[-1]



In [4]:
destination_folder = "images/"

# Ensure the destination folder exists
os.makedirs(destination_folder, exist_ok=True)

In [5]:
# Iterate through the 'picture' column and copy files
for file_path in df['file_path']:
    try:
        # Extract the filename from the file path
        file_name = os.path.basename(file_path)
        
        # Define the destination path
        destination_path = os.path.join(destination_folder, file_name)
        
        # Copy the file to the destination
        shutil.copy(file_path, destination_path)
        print(f"Copied: {file_path} to {destination_path}")
    except Exception as e:
        print(f"Error copying {file_path}: {e}")

Copied: face_recognition/lfw_funneled/Heath_Ledger/Heath_Ledger_0004.jpg to images/Heath_Ledger_0004.jpg
Copied: face_recognition/lfw_funneled/Heath_Ledger/Heath_Ledger_0001.jpg to images/Heath_Ledger_0001.jpg
Copied: face_recognition/lfw_funneled/Heath_Ledger/Heath_Ledger_0003.jpg to images/Heath_Ledger_0003.jpg
Copied: face_recognition/lfw_funneled/Heath_Ledger/Heath_Ledger_0002.jpg to images/Heath_Ledger_0002.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete_Sampras_0001.jpg to images/Pete_Sampras_0001.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete_Sampras_0002.jpg to images/Pete_Sampras_0002.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete_Sampras_0021.jpg to images/Pete_Sampras_0021.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete_Sampras_0014.jpg to images/Pete_Sampras_0014.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete_Sampras_0003.jpg to images/Pete_Sampras_0003.jpg
Copied: face_recognition/lfw_funneled/Pete_Sampras/Pete

In [6]:
#validation

In [7]:
import pandas as pd
from ultralytics import YOLO
import glob
import numpy as np
from utils import tune_parameters
import json
from config import *

In [8]:
#Parameters
metrics_list = ['euclidean', 'cosine']
thresholds = np.linspace(0, 0.5, 51)
layers_list = range(0, 7)

In [9]:
ground_truth_dict = df.groupby('cluster')['picture'].apply(list).to_dict()

In [ ]:
model = YOLO(MODEL_NAME)

In [11]:
model.predict('images/',classes=[0],save=True,
                    save_crop=True,project='humans',name="predict"
                    )



WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

image 1/9164 /home/sago/Documents/github/yolo-people-clustering/images/Aaron_Peirsol_0001.jpg: 640x640 1 person, 395.2ms
image 2/9164 /home/sago/Documents/github/yolo-people-clustering/images/Aaron_Peirsol_0002.jpg: 640x640 1 person, 231.9ms
image 3/9164 /home/sago/Documents/github/yolo-people-clustering/images/Aaron_Peirsol_0003.jpg: 640x640 1 person, 196.8ms
image 4/9164 /home/sago/Documents/github/yolo-people-clustering/images/Aaron_Peirsol_0004.jpg

[ultralytics.engine.results.Results object with attributes:
 
 boxes: ultralytics.engine.results.Boxes object
 keypoints: None
 masks: None
 names: {0: 'person', 1: 'bicycle', 2: 'car', 3: 'motorcycle', 4: 'airplane', 5: 'bus', 6: 'train', 7: 'truck', 8: 'boat', 9: 'traffic light', 10: 'fire hydrant', 11: 'stop sign', 12: 'parking meter', 13: 'bench', 14: 'bird', 15: 'cat', 16: 'dog', 17: 'horse', 18: 'sheep', 19: 'cow', 20: 'elephant', 21: 'bear', 22: 'zebra', 23: 'giraffe', 24: 'backpack', 25: 'umbrella', 26: 'handbag', 27: 'tie', 28: 'suitcase', 29: 'frisbee', 30: 'skis', 31: 'snowboard', 32: 'sports ball', 33: 'kite', 34: 'baseball bat', 35: 'baseball glove', 36: 'skateboard', 37: 'surfboard', 38: 'tennis racket', 39: 'bottle', 40: 'wine glass', 41: 'cup', 42: 'fork', 43: 'knife', 44: 'spoon', 45: 'bowl', 46: 'banana', 47: 'apple', 48: 'sandwich', 49: 'orange', 50: 'broccoli', 51: 'carrot', 52: 'hot dog', 53: 'pizza', 54: 'donut', 55: 'cake', 56: 'chair', 57: 'couch', 58: 'potted p

In [ ]:
distance_metrics = ['euclidean', 'cosine']
thresholds = np.linspace(0, 0.5, 51)
layers_list = range(0, 7)

In [ ]:
result = tune_parameters(model, layers_list, distance_metrics, thresholds, CROPS_PATH, list_imgs,ground_truth_dict)



WARNING ⚠️ inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

Results saved to discard/predict
AgglomerativeClustering(distance_threshold=np.float64(0.0), linkage='average',
                        metric='precomputed', n_clusters=None)
New Best - Metric: euclidean, Threshold: 0.0, Layer: 0, F1 Score: 0
AgglomerativeClustering(distance_threshold=np.float64(0.01), linkage='average',
                        metric='precomputed', n_clusters=None)
AgglomerativeClustering(distance_threshold=np.float64(0.02), linkage='

: 